developed by Chrisowalandis Deligio, Sebastian Gampe

In [1]:
import sys
sys.path.append("../")
import pandas as pd
import random
import os
import numpy as np
from cnt.model import (DesignEstimator, RelationExtractor, save_pipeline, load_pipeline, predict_re_single_sentence, 
relations_from_adjectives_df, relations_from_adjectives_single, concat_relations)
from cnt.annotate import (annotate, annotate_single_design, 
                          annotate_designs, 
                          extract_string_from_annotation, labeling_eng, labeling_eng_sub_verb)
from cnt.extract_relation import (path, NERTransformer, FeatureExtractor)
from cnt.evaluate import Metrics
from cnt.vectorize import (Doc2Str, Path2Str, Verbs2Str, AveragedPath2Vec, 
                           AveragedRest2Vec)
from cnt.io import (replace_left_right)
from cnt.io import  Database_Connection
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline, make_pipeline, make_union
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import Normalizer
from sklearn.naive_bayes import MultinomialNB
from itertools import product
import warnings
warnings.filterwarnings('ignore')

In [2]:
# Database access in text file: "mysql+mysqlconnector://root:YourConnection" -> Format user:password@IP/Database
f = open("/home/bigdatalab/Projects/D4N4/NLP_release_1.0/db_access.txt", "r")
access = f.read()
dc =  Database_Connection(access)

In [3]:
id_col = "id"
design_col = "design_en"

In [4]:
import yaml
import_path = "../data/English_RE_data_Subj-Verb.yaml" # English_RE_data_new.yaml"
with open(import_path, encoding='utf8') as f:
    dictionary = yaml.safe_load(f)
    d = {replace_left_right(key): value for key, value in dictionary.items()}

In [5]:
# new gt from datachallenge
new_gt = pd.read_csv('/home/bigdatalab/Projects/D4N4/NLP_release_1.0/DataChallenge_LLM_REPipeline/new_gt.csv')
new_gt.head().style

In [108]:
# new gt
new_gt = new_gt.drop(columns=['l_spo_long', 'l_spo_short_gt', 'comparison_result'],  axis=1)
new_gt = new_gt.rename(columns={"design_id": "id", "design_en": "design_en", "l_spo_short_new": "y"})
col = new_gt.pop("id")
new_gt.insert(len(new_gt.columns), 'id', col)
new_gt.head().style

In [109]:
# new gt
d2 = new_gt
d2['db_id'] = new_gt['id']

In [110]:
#new gt
d2

design_en  \
0    Bust of youthful Anchialos, right, wearing tae...   
1    Wreath bust of Antoninus Pius, right, wearing ...   
2    Wreath bust of Antoninus Pius, right, wearing ...   
3    Half-nude Aphrodite standing facing, head left...   
4    Nude Aphrodite standing facing, head right, ho...   
..                                                 ...   
531  Ares standing left, wearing helmet, holding sh...   
532  Athena seated_on left, wearing a Corinthian he...   
533  Nude bearded Heracles standing in lowered posi...   
534  Athena seated_on left, wearing a Corinthian he...   
535  Roma seated_on left on cuirass, holding Nike a...   

                                                     y    id  db_id  
0    [('Anchialos', 'PERSON', 'wearing', 'taenia', ...    10     10  
1    [('Antoninus Pius', 'PERSON', 'wearing', 'cuir...    27     27  
2    [('Antoninus Pius', 'PERSON', 'wearing', 'palu...    28     28  
3    [('Aphrodite', 'PERSON', 'holding', 'apple', '...    33     33  
4    [('Aphrodite', 'PERSON', 'holding', 'breast', ...    36     36  
..                                                 ...   ...    ...  
531  [('Ares', 'PERSON', 'wearing', 'helmet', 'OBJE...  4124   4124  
532  [('Athena', 'PERSON', 'wearing', 'helmet', 'OB...  4190   4190  
533  [('Heracles', 'PERSON', 'strangling', 'Nemean ...  4276   4276  
534  [('Athena', 'PERSON', 'wearing', 'helmet', 'OB...  4377   4377  
535  [('Roma', 'PERSON', 'seated_on', 'cuirass', 'O...  4382   4382  

[536 rows x 4 columns]

In [5]:
relation_counts = {}
labels = []
for sentence, relations in d.items():
    for rel in relations:
        rel_name = rel[1]
        if rel_name not in relation_counts:
            relation_counts[rel_name] = 1
        else:
            relation_counts[rel_name] += 1

sorted(relation_counts.items(), key= lambda x: (-x[1], x[0]))

[('holding', 679),
 ('standing', 564),
 ('wearing', 369),
 ('resting', 189),
 ('seated', 93),
 ('advancing', 71),
 ('enthroned', 68),
 ('curling', 65),
 ('riding', 45),
 ('reclining', 34),
 ('lying', 33),
 ('leaping', 31),
 ('coiling', 26),
 ('prancing', 25),
 ('sailing', 16),
 ('swimming', 15),
 ('drawing', 13),
 ('leaning', 13),
 ('crowning', 12),
 ('raising', 12),
 ('feeding', 11),
 ('flying', 9),
 ('grasping', 8),
 ('strangling', 8),
 ('kneeling', 5),
 ('extending', 4),
 ('pushing', 4),
 ('sitting', 4),
 ('clasping', 3),
 ('crossing', 3),
 ('galloping', 3),
 ('receiving', 3),
 ('running', 3),
 ('setting', 3),
 ('carrying', 2),
 ('creeps', 2),
 ('jumping', 2),
 ('containing', 1),
 ('covering', 1),
 ('ears', 1),
 ('forming', 1),
 ('galopping', 1),
 ('leaned', 1),
 ('playing', 1),
 ('ploughing', 1),
 ('walking', 1)]

In [6]:
language = "_en"
add_columns = ["name"+language, "alternativenames"+language] #["id", "name"+language, "alternativenames"+language]

In [7]:
entities = {
    "PERSON": dc.load_entities_from_db("nlp_list_person", ["name", "alternativenames"], ["alternativenames"], ",", True),
    "OBJECT": dc.load_entities_from_db("nlp_list_obj", add_columns, [add_columns[1]], ",", True),
    "ANIMAL": dc.load_entities_from_db("nlp_list_animal", add_columns, [add_columns[1]], ",", True),
    "PLANT": dc.load_entities_from_db("nlp_list_plant", add_columns, [add_columns[1]], ",", True)}

In [8]:
X_list, y_list = labeling_eng_sub_verb(d, entities) #labeling_eng for subj verb obj, 
# labeling_eng_sub_verb for subj verb verb

In [9]:
X = pd.DataFrame({design_col: X_list, "y" : y_list})

In [10]:
X.shape

(987, 2)

In [11]:
X[id_col] = X.index

In [12]:
X.style

In [13]:
for index, row in X.iterrows():
    if "'" in row["design_en"]:
        X.at[index, "design_en"] = row["design_en"].replace("'", "\\'")

In [14]:
X.style

In [15]:
def get_id(design):
    try:
        return (dc.create_own_query("select id from nlp_training_designs where design_en='"+design+"';").id)[0]
    except:
        return "Null"

In [16]:
%%capture
X["db_id"] = X.apply(lambda row: get_id(row.design_en), axis=1)

In [17]:
X.style

In [18]:
X[X['db_id'] == 'Null'].style

In [19]:
X.shape

(987, 4)

In [20]:
X = X.loc[X.db_id!="Null"]

In [21]:
X.shape

(899, 4)

In [22]:
X.head(5)

design_en  \
0  Amphora with ribbed surface and crooked handle...   
1  Bust of youthful Anchialos, right, wearing tae...   
2  Bare-headed bust of Antoninus Pius, right, wea...   
3  Laureate bust of Antoninus Pius, right, wearin...   
4  Laureate bust of Antoninus Pius, right, wearin...   

                                                   y  id db_id  
0  [(Amphora, OBJECT, containing, containing, VERB)]   0     9  
1      [(Anchialos, PERSON, wearing, wearing, VERB)]   1    10  
2  [(Antoninus Pius, PERSON, wearing, wearing, VE...   2    24  
3  [(Antoninus Pius, PERSON, wearing, wearing, VE...   3    27  
4  [(Antoninus Pius, PERSON, wearing, wearing, VE...   4    28

In [23]:
entities = dc.create_own_query("select * from nlp_list_entities;")

In [24]:
entities[["id", "name_en", "alternativenames_en"]]

id      name_en alternativenames_en
0       1   Abundantia                None
1       2      Actaeon                None
2       3     Aemilian                None
3       4       Aeneas                None
4       5     Aequitas             Equitas
..    ...          ...                 ...
844   845      turning                None
845   846      sailing                None
846   847  escorted_by         escorted by
847   848      wearing                None
848  1000     no-value                None

[849 rows x 3 columns]

In [25]:
ent_dict = {}
for index, row in entities[["id", "name_en", "alternativenames_en"]].iterrows():
    ent_dict[row["id"]] = (row["name_en"]+", "+row["alternativenames_en"]).replace(", None","")#.lower()

In [26]:
result1 = pd.DataFrame(columns=["design_id", "subject", "subject_str", "predicate", "predicate_str", "object", "object_str"])

In [112]:
# new gt
result2 = pd.DataFrame(columns=["design_id", "subject", "subject_str", "predicate", "predicate_str", "object", "object_str"])

In [27]:
def get_id(ent):
    for row in ent_dict:
        for entry in ent_dict[row].split(', '):
            if ent == entry:
                return row
            if ent.lower() == entry:
                return row
    return ent

In [28]:
for index, row in X.iterrows():
    for y in row.y:
        subject = get_id(y[0])
        subject_str = y[0]
        predicate = get_id(y[2])
        predicate_str = y[2]
        obj = get_id(y[3])
        obj_str = y[3]
        if type(subject) == int and type(predicate) == int and type(obj) == int:
            result1 = result1._append({"design_id": row.db_id, 
                                     "subject": subject, 
                                     "subject_str": subject_str,
                                     "predicate": predicate, 
                                     "predicate_str": predicate_str,
                                     "object": obj,
                                     "object_str": obj_str}, ignore_index=True)
        else:
            print(subject, predicate, obj)

29 playing playing
772 creeps creeps
772 creeps creeps
165 strangling strangling
165 strangling strangling
165 strangling strangling
165 strangling strangling
165 strangling strangling
165 strangling strangling
165 strangling strangling
304 leaned leaned
165 strangling strangling


In [113]:
# new gt
import ast

for index, row in d2.iterrows():
    y_list = ast.literal_eval(row["y"])
    #print(y_list)
    for y in y_list:
        print(y)
        subject = get_id(y[0])
        subject_str = y[0]
        predicate = get_id(y[2])
        predicate_str = y[2]
        obj = get_id(y[3])
        obj_str = y[3]
        if type(subject) == int and type(predicate) == int and type(obj) == int:
            result2 = result2._append({"design_id": row.db_id, 
                                     "subject": subject, 
                                     "subject_str": subject_str,
                                     "predicate": predicate, 
                                     "predicate_str": predicate_str,
                                     "object": obj,
                                     "object_str": obj_str}, ignore_index=True)
        else:
            print(subject, predicate, obj)

('Anchialos', 'PERSON', 'wearing', 'taenia', 'OBJECT')
('Antoninus Pius', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Antoninus Pius', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Antoninus Pius', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Aphrodite', 'PERSON', 'holding', 'apple', 'PLANT')
('Aphrodite', 'PERSON', 'holding', 'breast', 'OBJECT')
('Aphrodite', 'PERSON', 'holding', 'pudenda', 'OBJECT')
27 826 pudenda
('Eros', 'PERSON', 'seated_on', 'dolphin', 'ANIMAL')
('Apollo', 'PERSON', 'holding', 'arrow', 'OBJECT')
('Apollo', 'PERSON', 'holding', 'bow', 'OBJECT')
('Apollo', 'PERSON', 'seated_on', 'omphalos', 'OBJECT')
('Apollo', 'PERSON', 'holding', 'bow', 'OBJECT')
('Apollo', 'PERSON', 'seated_on', 'omphalos', 'OBJECT')
('Apollo', 'PERSON', 'holding', 'bow', 'OBJECT')
('Apollo', 'PERSON', 'holding', 'patera', 'OBJECT')
('Apollo', 'PERSON', 'holding', 'bow', 'OBJECT')
('Apollo', 'PERSON', 'resting_on', 'garland', 'OBJECT')
('Apollo', 'PERSON', 'resting_on', 'column', 'OBJECT'

('Charis', 'PERSON', 'holding', 'jar', 'OBJECT')
('Charis', 'PERSON', 'holding', 'corn', 'PLANT')
('nymph', 'PERSON', 'wearing', 'garment', 'OBJECT')
('nymph', 'PERSON', 'holding', 'jar', 'OBJECT')
('nymph', 'PERSON', 'holding', 'corn', 'PLANT')
('Charis', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Charis', 'PERSON', 'holding', 'vase', 'OBJECT')
('nymph', 'PERSON', 'wearing', 'garment', 'OBJECT')
('nymph', 'PERSON', 'holding', 'vase', 'OBJECT')
('Charis', 'PERSON', 'holding', 'nymph', 'PERSON')
('Charis', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Charis', 'PERSON', 'holding', 'spindel', 'OBJECT')
68 826 spindel
('nymph', 'PERSON', 'wearing', 'garment', 'OBJECT')
('nymph', 'PERSON', 'holding', 'spindel', 'OBJECT')
264 826 spindel
('Charis', 'PERSON', 'holding', 'nymph', 'PERSON')
('Charis', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Charis', 'PERSON', 'holding', 'amphora', 'OBJECT')
('nymph', 'PERSON', 'wearing', 'garment', 'OBJECT')
('nymph', 'PERSON', 'holding', 'amphora', 'OBJECT

('Faustina Minor', 'PERSON', 'holding', 'patera', 'OBJECT')
('Faustina Minor', 'PERSON', 'holding', 'scepter', 'OBJECT')
('Severus Alexander', 'PERSON', 'seated_on', 'horse', 'ANIMAL')
('Severus Alexander', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Severus Alexander', 'PERSON', 'holding', 'spear', 'OBJECT')
('Philippus Arabs', 'PERSON', 'seated_on', 'horse', 'ANIMAL')
('Philippus Arabs', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Philippus Arabs', 'PERSON', 'holding', 'scepter', 'OBJECT')
('Commodus', 'PERSON', 'seated_on', 'horse', 'ANIMAL')
('Commodus', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Commodus', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Commodus', 'PERSON', 'wearing', 'boot', 'OBJECT')
('Commodus', 'PERSON', 'holding', 'spear', 'OBJECT')
('Caracalla', 'PERSON', 'seated_on', 'horse', 'ANIMAL')
('Caracalla', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Caracalla', 'PERSON', 'holding', 'scepter', '

('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'altar', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Homonoia', 'PERSON', 'wearing', 'kalathos', 'OBJECT')
('Homonoia', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'altar', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Homonoia', 'PERSON', 'wearing', 'kalathos', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'altar', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Demeter', 'PERSON', 'holding', 'corn', 'PLANT')
('Homonoia', 'PERSON', 'wearing', 'kalathos', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Demeter', 'PERSON', 'standing', 'Homonoia', 'PERSON')
('Hygieia', 'PERSON', 'feeding', 'serpent', 'ANIMAL')
('Hygieia'

('Elagabalus', 'PERSON', 'with', 'aegis', 'OBJECT')
118 with 416
('Nemesis', 'PERSON', 'plucking', 'chiton', 'OBJECT')
253 plucking 466
('Nemesis', 'PERSON', 'holding', 'rein', 'OBJECT')
('Nemesis', 'PERSON', 'at her foot', 'wheel', 'OBJECT')
253 at her foot 669
('Severus Alexander', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Severus Alexander', 'PERSON', 'with', 'aegis', 'OBJECT')
347 with 416
('Severus Alexander', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Severus Alexander', 'PERSON', 'with', 'aegis', 'OBJECT')
347 with 416
('Athena', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Athena', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Athena', 'PERSON', 'holding', 'patera', 'OBJECT')
('Athena', 'PERSON', 'resting_on', 's

('Septimius Severus', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Septimius Severus', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Tyche', 'PERSON', 'holding', 'temple', 'OBJECT')
('Tyche', 'PERSON', 'over', 'altar', 'OBJECT')
383 over 418
('Heracles', 'PERSON', 'grasping', 'horn', 'OBJECT')
('Heracles', 'PERSON', 'strangling', 'Cretan Bull', 'ANIMAL')
165 strangling 734
('Heracles', 'PERSON', 'holding', 'hind', 'ANIMAL')
('Heracles', 'PERSON', 'wearing', 'lion skin', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'antlers', 'OBJECT')
('Heracles', 'PERSON', 'lying', 'club', 'OBJECT')
('Cybele', 'PERSON', 'throne', 'throne', 'OBJECT')
('Cybele', 'PERSON', 'holding', 'patera', 'OBJECT')
('Cybele', 'PERSON', 'resting_on', 'tympanon', 'OBJECT')
('Attis', 'PERSON', 'wearing', 'cap', 'OBJECT')
('Attis', 'PERSON', 'holding', 'pedum', 'OBJECT')
('Cybele', 'PERSON', 'seated_on', 'lion', 'ANIMAL')
('Athena', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Athena', 'PERSON', 'wearing', 'garment', 'OB

('Heracles', 'PERSON', 'resting', 'lion skin', 'OBJECT')
('Heracles', 'PERSON', 'resting', 'club', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'lion skin', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'club', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'patera', 'OBJECT')
('Heracles', 'PERSON', 'over', 'garland', 'OBJECT')
165 over 513
('Heracles', 'PERSON', 'over', 'altar', 'OBJECT')
165 over 418
('eagle', 'ANIMAL', 'flying', 'altar', 'OBJECT')
('Nemesis', 'PERSON', 'holding', 'scales', 'OBJECT')
('Nemesis', 'PERSON', 'holding', 'rein', 'OBJECT')
('Aequitas', 'PERSON', 'holding', 'scales', 'OBJECT')
('Aequitas', 'PERSON', 'holding', 'rein', 'OBJECT')
('Emperor', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Emperor', 'PERSON', 'wearing', 'paludamentum', 'OBJECT')
('Emperor', 'PERSON', 'holding', 'patera', 'OBJECT')
('Emperor', 'PERSON', 'over', 'altar', 'OBJECT')
119 over 418
('Emperor', 'PERSON', 'resting_on', 'scepter', 'OBJECT')
('Severus Alexander', 'PERSON', 'wearing', 'cuirass', 'O

('Athena', 'PERSON', 'wearing', 'chiton', 'OBJECT')
('Athena', 'PERSON', 'holding', 'spear', 'OBJECT')
('Athena', 'PERSON', 'holding', 'shield', 'OBJECT')
('Athena', 'PERSON', 'holding', 'tree', 'PLANT')
('tree', 'PLANT', 'entwined', 'serpent', 'ANIMAL')
822 entwined 772
('Hermes', 'PERSON', 'wearing', 'petasus', 'OBJECT')
('Alexander the Great', 'PERSON', 'wearing', 'lion skin', 'OBJECT')
('Cybele', 'PERSON', 'wearing', 'throne', 'OBJECT')
('Cybele', 'PERSON', 'wearing', 'polos', 'OBJECT')
('Cybele', 'PERSON', 'holding', 'patera', 'OBJECT')
('Cybele', 'PERSON', 'holding', 'scepter', 'OBJECT')
('lion', 'ANIMAL', 'under', 'throne', 'OBJECT')
758 under 644
('Dionysus', 'PERSON', 'wearing', 'taenia', 'OBJECT')
('Dionysus', 'PERSON', 'wearing', 'ivy wreath', 'OBJECT')
('ivy wreath', 'OBJECT', 'with', 'leaf', 'PLANT')
530 with 808
('ivy wreath', 'OBJECT', 'with', 'fruit', 'PLANT')
530 with 802
('Athena', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Artemis', 'PERSON', 'wearing', 'chiton', 'OB

('Ares', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Ares', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Ares', 'PERSON', 'wearing', 'boot', 'OBJECT')
('Ares', 'PERSON', 'holding', 'spear', 'OBJECT')
('Ares', 'PERSON', 'holding', 'shield', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'club', 'OBJECT')
('Heracles', 'PERSON', 'holding', 'cantharus', 'OBJECT')
('Heracles', 'PERSON', 'over', 'lion skin', 'OBJECT')
165 over 544
('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Homonoia', 'PERSON', 'wearing', 'kalathos', 'OBJECT')
('Homonoia', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'patera', 'OBJECT')
('Homonoia', 'PERSON', 'holding', 'cornucopia', 'OBJECT')
('Septimius Severus', 'PERSON', 'wearing', 'cuirass', 'OBJECT')
('Septimius Severus', 'PERSON', 'wearing', 'boot', 'OBJECT')
('Septimius Severus', 'PERSON', 'holding', 'globe', 'OBJECT')
('Septimius Severus', 'PERSON', 'holding', 'spear', 'O

('athlete', 'PERSON', 'holding', 'object', 'OBJECT')
('Charis', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Charis', 'PERSON', 'holding', 'vase', 'OBJECT')
('Hera', 'PERSON', 'wearing', 'kalathos', 'OBJECT')
('Hera', 'PERSON', 'wearing', 'garment', 'OBJECT')
('Hera', 'PERSON', 'holding', 'patera', 'OBJECT')
('Hera', 'PERSON', 'resting_on', 'scepter', 'OBJECT')
('Ares', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Ares', 'PERSON', 'holding', 'shield', 'OBJECT')
('Athena', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Athena', 'PERSON', 'holding', 'patera', 'OBJECT')
('Athena', 'PERSON', 'holding', 'spear', 'OBJECT')
('Heracles', 'PERSON', 'strangling', 'Nemean lion', 'ANIMAL')
165 strangling 759
('Heracles', 'PERSON', 'under', 'club', 'OBJECT')
165 under 476
('Nemean lion', 'ANIMAL', 'under', 'club', 'OBJECT')
759 under 476
('Athena', 'PERSON', 'wearing', 'helmet', 'OBJECT')
('Athena', 'PERSON', 'holding', 'patera', 'OBJECT')
('Athena', 'PERSON', 'holding', 'spear', 'OBJECT')
('Athena', 'PER

In [29]:
result1.style

In [34]:
result1.shape

(2067, 7)

In [114]:
# new_gt
result2.style

In [124]:
# new gt
result2.shape

(1383, 7)

In [117]:
# get design ids from new gt
ids = result2['design_id'].to_list()
ids = list(set(ids))
ids.sort()
len(ids)

533

In [123]:
# filter old gt with ids from new gt
result_all = result1.loc[~result1['design_id'].isin(ids)]
result_all.shape

(1003, 7)

In [125]:
# merge old gt and new gt
frames = [result_all, result2]
result_all = pd.concat(frames)
result_all.shape

(2386, 7)

In [30]:
result_all.to_sql("nlp_relation_extraction_en_sub_verb",dc.mysql_connection,if_exists="append", index=False)

2067